<a href="https://colab.research.google.com/github/marcosilvaa/dados_estudos/blob/main/Backtesting_VectorBT_com_Python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install vectorbt
!pip install yfinance
!pip install ta
!pip install pandas_ta
!pip install TA-Lib
!pip install talib-binary
!pip install plotly

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached TA-Lib-0.4.25.tar.gz (271 kB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
  error: subprocess-exited-with-error
  
  × Building wheel for TA-Lib (pyproject.toml) did not run successfully.
  │ exit code: 1
  ╰─> See above for output.
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
  ERROR: Failed building wheel fo

In [ ]:
# Importando bilbiotecas

#Análise de dados
import pandas as pd
import numpy as np

#Cotações
import yfinance as yf

#Backtesting
import vectorbt as vbt

#Análise técnica
import ta
import pandas_ta

#Gráfigo
import plotly.graph_objects as go

#Obtendo Dados
A biblioteca VectorBT tem integração direta com outras bibliotecas como Yahoo Finance, tornando possível o download direto via método. É possível também utilizar sua propria base de dados para realizar as análises.

In [ ]:
# criando variavel que vai fazer o download
# btc = vbt.YFData.download("BTC-USD", period="max",interval="1d") ---> coletando periodo maximo

# PARAMETRO ---> missing_index="drop"
# mais utilizado para mercados que fecham no fim de semana, deixa no DF somente os valores que não são do tipo NaN 

# Definindo range da data de download.  -> a partir do terceiro ciclo
btc_D = vbt.YFData.download("BTC-USD",start="2016-06-16", end="now",interval="1d")

# Também posso passar o método .get() logo apos a chamada do download
#Ou como abaixo, chamar o método direto da variavel recem criada

In [ ]:
btc_ohlc = btc_D.get(["Open","High","Low","Close"])
btc_ohlc.head()

Open        High         Low       Close
Date                                                                     
2016-06-16 00:00:00+00:00  696.523010  773.721985  696.523010  766.307983
2016-06-17 00:00:00+00:00  768.487000  775.356018  716.556030  748.908997
2016-06-18 00:00:00+00:00  748.755981  777.989990  733.929016  756.226990
2016-06-19 00:00:00+00:00  756.687988  766.620972  745.627991  763.781006
2016-06-20 00:00:00+00:00  763.927002  764.083984  732.726990  737.226013

In [ ]:
# Também é possivel 
btc_vol = btc_D.get(["Volume"])
btc_vol.tail()

Volume
Date                                  
2023-02-25 00:00:00+00:00  16100721565
2023-02-26 00:00:00+00:00  16644534842
2023-02-27 00:00:00+00:00  22660763494
2023-02-28 00:00:00+00:00  20535363434
2023-03-01 00:00:00+00:00  25003618304

#Plotando gráficos

A vectorbt também tem integração com a biblioteca plotly, facilitando o processo de plotagem de gráficos, assim como a edição do layout dos mesmos. 

In [ ]:
# VectorBT já tem integração com a lib plotly
# é possivel plotar diretamente com ela

btc_ohlc["Close"].vbt.plot(
    width=800,
    height=500,
    template="simple_white",
    paper_bgcolor="gray",
    title_text="Preço BTC"
).update_traces(line=dict(color="black", width=5, dash="dot")).update_xaxes(title_text="Data").update_yaxes(title_text="BITCOIN", type="log").show()

###Plot comparativo

Agora vamos comparar o desempenho entre dois ativos.
Aqui vamos utilizar o índice do dolar (DXY), contra o índice das 500 maiores empresas dos Estados Unidos S&P500(SPX).

In [ ]:
usd_spx = vbt.YFData.download(["DX-Y.NYB","^GSPC"], start='2 year', end='now', interval='1d', missing_index="drop").get('Close')
usd_spx

/usr/local/lib/python3.8/dist-packages/vectorbt/data/base.py:527: UserWarning:

Symbols have mismatching index. Dropping missing data points.



symbol                       DX-Y.NYB        ^GSPC
Date                                              
2021-03-01 05:00:00+00:00   91.040001  3901.820068
2021-03-02 05:00:00+00:00   90.790001  3870.290039
2021-03-03 05:00:00+00:00   90.949997  3819.719971
2021-03-04 05:00:00+00:00   91.629997  3768.469971
2021-03-05 05:00:00+00:00   91.980003  3841.939941
...                               ...          ...
2023-02-23 05:00:00+00:00  104.599998  4012.320068
2023-02-24 05:00:00+00:00  105.209999  3970.040039
2023-02-27 05:00:00+00:00  104.669998  3982.239990
2023-02-28 05:00:00+00:00  104.870003  3970.149902
2023-03-01 05:00:00+00:00  104.524002  3947.520020

[505 rows x 2 columns]

In [ ]:
#Renomeando colunas
usd_spx = usd_spx.rename(columns={
    "DX-Y.NYB":"DXY","^GSPC":"SPX"
})

Para fazer essa comparação, devemos normalizar os preços, para isso vamos dividir todo o dataframe pelo valor da primeira linha. 

In [ ]:
###Normalizar os preços
#divide todo o dataframe pelo primeiro valor
usd_spx_norm = usd_spx/usd_spx.iloc[0]
usd_spx_norm.head()

symbol                          DXY       SPX
Date                                         
2021-03-01 05:00:00+00:00  1.000000  1.000000
2021-03-02 05:00:00+00:00  0.997254  0.991919
2021-03-03 05:00:00+00:00  0.999011  0.978959
2021-03-04 05:00:00+00:00  1.006481  0.965824
2021-03-05 05:00:00+00:00  1.010325  0.984653

In [ ]:
#Plot comparativo
usd_spx_norm["DXY"].vbt.plot_against(usd_spx_norm["SPX"]).show()

In [ ]:
# Agora com a função pct_change() vamos análisar a variação percentual de ambos os ativos
usd_spx_var = usd_spx.pct_change().dropna()
usd_spx_var.tail()

symbol                          DXY       SPX
Date                                         
2023-02-23 05:00:00+00:00  0.000096  0.005329
2023-02-24 05:00:00+00:00  0.005832 -0.010538
2023-02-27 05:00:00+00:00 -0.005133  0.003073
2023-02-28 05:00:00+00:00  0.001911 -0.003036
2023-03-01 05:00:00+00:00 -0.003299 -0.005700

In [ ]:
# Vamos analisar a variação mensal
# Para isso vamos criar uma nova coluna que vai armazenar o mês de cada dado
usd_spx_var["Mes"] = usd_spx_var.index.strftime("%m")
usd_spx_var.tail()

symbol                          DXY       SPX Mes
Date                                             
2023-02-23 05:00:00+00:00  0.000096  0.005329  02
2023-02-24 05:00:00+00:00  0.005832 -0.010538  02
2023-02-27 05:00:00+00:00 -0.005133  0.003073  02
2023-02-28 05:00:00+00:00  0.001911 -0.003036  02
2023-03-01 05:00:00+00:00 -0.003299 -0.005700  03

In [ ]:
#Plotando heatmap com a mediana da variação % mensal
usd_spx_var.groupby(["Mes"]).median().vbt.ts_heatmap().show()

In [ ]:
#Plotando heatmap com o desvio padrão da variação mensal. ---> Volatilidade
usd_spx_var.groupby(["Mes"]).std().vbt.ts_heatmap().show()

#Plotando Gráfico OHLC
Através da integração com a plotly vamos plotar o gráfico do Ethereum com os dados coletados da Yahoo Finance.

In [ ]:
# Coletando dados do ethereum
eth = vbt.YFData.download("ETH-USD", start="1 year", end="now", interval="1d").get(["Open","High","Low","Close","Volume"])

In [ ]:
# Plotando Gráfico
eth.vbt.ohlcv.plot().show()

#Indicadores no gráfico
Vamos construir os indicadores e definir os seu parâmetros, então plotar de forma direta com a VectorBT

In [ ]:
#Construindo indicador de Bandas de Bollinger de 20 períodos
bb_20p_middle = vbt.BBANDS.run(eth.Close,20).middle
bb_20p_upper = vbt.BBANDS.run(eth.Close,20).upper
bb_20p_low = vbt.BBANDS.run(eth.Close,20).lower
#plotando
vbt.BBANDS.run(eth.Close, 20).plot().show()

In [ ]:
#coletando dados do BTC através da variável que foi criada no começo do Notebook
btc = btc_D.get(["Close"]).round(2)
btc.tail()

Close
Date                               
2023-02-25 00:00:00+00:00  23175.38
2023-02-26 00:00:00+00:00  23561.21
2023-02-27 00:00:00+00:00  23522.87
2023-02-28 00:00:00+00:00  23147.35
2023-03-01 00:00:00+00:00  23701.90

In [ ]:
# Calculando valor da média movel e adicionando ao dataframe
MM_20p = vbt.MA.run(btc.Close, 20).ma
btc["MMA20"] = MM_20p
btc.tail()

Close       MMA20
Date                                           
2023-02-25 00:00:00+00:00  23175.38  23268.1585
2023-02-26 00:00:00+00:00  23561.21  23308.2135
2023-02-27 00:00:00+00:00  23522.87  23321.1425
2023-02-28 00:00:00+00:00  23147.35  23331.5400
2023-03-01 00:00:00+00:00  23701.90  23425.6830

In [ ]:
# calculando media movel como objeto para entao plotar de forma direta sem salvar os valores
MM_20p_obj = vbt.MA.run(btc.Close, 20)
MM_20p_obj

In [ ]:
MM_20p_obj.plot().show()

In [ ]:
### Calculando diversas médias de uma unica vez atraves de um dicionario
MM_varias = vbt.MA.run(btc.Close,[8,9,17,21,50,100,200]).ma
MM_varias.tail()

ma_window                          8             9             17   \
Date                                                                 
2023-02-25 00:00:00+00:00  24093.03250  24145.540000  23317.610000   
2023-02-26 00:00:00+00:00  23958.02375  24033.941111  23420.090588   
2023-02-27 00:00:00+00:00  23857.42750  23909.673333  23530.190000   
2023-02-28 00:00:00+00:00  23647.20250  23778.530000  23605.276471   
2023-03-01 00:00:00+00:00  23555.39625  23653.280000  23717.847059   

ma_window                           21          50          100          200  
Date                                                                          
2023-02-25 00:00:00+00:00  23253.278095  22188.4506  19496.6076  19760.12025  
2023-02-26 00:00:00+00:00  23282.113333  22320.5732  19565.2419  19758.18810  
2023-02-27 00:00:00+00:00  23318.435238  22449.2078  19633.3551  19756.01480  
2023-02-28 00:00:00+00:00  23312.866667  22568.2238  19701.9103  19749.73745  
2023-03-01 00:00:00+00:00  23349.176190  22693.3360  19781.0565  19746.12660

In [ ]:
# concatenando DFs
btc = pd.concat([btc, MM_varias], axis=1)
btc.tail()

Close       MMA20            8             9  \
Date                                                                         
2023-02-25 00:00:00+00:00  23175.38  23268.1585  24093.03250  24145.540000   
2023-02-26 00:00:00+00:00  23561.21  23308.2135  23958.02375  24033.941111   
2023-02-27 00:00:00+00:00  23522.87  23321.1425  23857.42750  23909.673333   
2023-02-28 00:00:00+00:00  23147.35  23331.5400  23647.20250  23778.530000   
2023-03-01 00:00:00+00:00  23701.90  23425.6830  23555.39625  23653.280000   

                                     17            21          50         100  \
Date                                                                            
2023-02-25 00:00:00+00:00  23317.610000  23253.278095  22188.4506  19496.6076   
2023-02-26 00:00:00+00:00  23420.090588  23282.113333  22320.5732  19565.2419   
2023-02-27 00:00:00+00:00  23530.190000  23318.435238  22449.2078  19633.3551   
2023-02-28 00:00:00+00:00  23605.276471  23312.866667  22568.2238  19701.9103   
2023-03-01 00:00:00+00:00  23717.847059  23349.176190  22693.3360  19781.0565   

                                   200  
Date                                    
2023-02-25 00:00:00+00:00  19760.12025  
2023-02-26 00:00:00+00:00  19758.18810  
2023-02-27 00:00:00+00:00  19756.01480  
2023-02-28 00:00:00+00:00  19749.73745  
2023-03-01 00:00:00+00:00  19746.12660

In [ ]:
### Media Exponencial
# basta inserir o parâmetro ewm=True
btc["EMA9"] = vbt.MA.run(btc.Close,9, short_name="EMA9", ewm=True).ma
btc.tail()

Close       MMA20            8             9  \
Date                                                                         
2023-02-25 00:00:00+00:00  23175.38  23268.1585  24093.03250  24145.540000   
2023-02-26 00:00:00+00:00  23561.21  23308.2135  23958.02375  24033.941111   
2023-02-27 00:00:00+00:00  23522.87  23321.1425  23857.42750  23909.673333   
2023-02-28 00:00:00+00:00  23147.35  23331.5400  23647.20250  23778.530000   
2023-03-01 00:00:00+00:00  23701.90  23425.6830  23555.39625  23653.280000   

                                     17            21          50         100  \
Date                                                                            
2023-02-25 00:00:00+00:00  23317.610000  23253.278095  22188.4506  19496.6076   
2023-02-26 00:00:00+00:00  23420.090588  23282.113333  22320.5732  19565.2419   
2023-02-27 00:00:00+00:00  23530.190000  23318.435238  22449.2078  19633.3551   
2023-02-28 00:00:00+00:00  23605.276471  23312.866667  22568.2238  19701.9103   
2023-03-01 00:00:00+00:00  23717.847059  23349.176190  22693.3360  19781.0565   

                                   200          EMA9  
Date                                                  
2023-02-25 00:00:00+00:00  19760.12025  23715.967607  
2023-02-26 00:00:00+00:00  19758.18810  23685.016086  
2023-02-27 00:00:00+00:00  19756.01480  23652.586869  
2023-02-28 00:00:00+00:00  19749.73745  23551.539495  
2023-03-01 00:00:00+00:00  19746.12660  23581.611596

In [ ]:
### RSI
ifr = vbt.RSI.run(btc.Close, window=17).rsi
btc["RSI"] = ifr
btc.tail()

Close       MMA20            8             9  \
Date                                                                         
2023-02-25 00:00:00+00:00  23175.38  23268.1585  24093.03250  24145.540000   
2023-02-26 00:00:00+00:00  23561.21  23308.2135  23958.02375  24033.941111   
2023-02-27 00:00:00+00:00  23522.87  23321.1425  23857.42750  23909.673333   
2023-02-28 00:00:00+00:00  23147.35  23331.5400  23647.20250  23778.530000   
2023-03-01 00:00:00+00:00  23701.90  23425.6830  23555.39625  23653.280000   

                                     17            21          50         100  \
Date                                                                            
2023-02-25 00:00:00+00:00  23317.610000  23253.278095  22188.4506  19496.6076   
2023-02-26 00:00:00+00:00  23420.090588  23282.113333  22320.5732  19565.2419   
2023-02-27 00:00:00+00:00  23530.190000  23318.435238  22449.2078  19633.3551   
2023-02-28 00:00:00+00:00  23605.276471  23312.866667  22568.2238  19701.9103   
2023-03-01 00:00:00+00:00  23717.847059  23349.176190  22693.3360  19781.0565   

                                   200          EMA9        RSI  
Date                                                             
2023-02-25 00:00:00+00:00  19760.12025  23715.967607  51.424769  
2023-02-26 00:00:00+00:00  19758.18810  23685.016086  61.542427  
2023-02-27 00:00:00+00:00  19756.01480  23652.586869  62.617074  
2023-02-28 00:00:00+00:00  19749.73745  23551.539495  58.427647  
2023-03-01 00:00:00+00:00  19746.12660  23581.611596  61.893752

In [ ]:
# plotando RSI separadamente
vbt.RSI.run(btc.Close, window=17).plot().show()

# Sinais de Trading
A vectorbt retorna TRUE quando algum sinal que configurarmos for ativado, é possível atribuir esse resultado à uma coluna do DataFrame.

##Cross Above and Cross Below

In [ ]:
btc.dropna(inplace=True)

In [ ]:
btc.tail().round(2)

Close     MMA20         8         9        17  \
Date                                                                          
2023-02-25 00:00:00+00:00  23175.38  23268.16  24093.03  24145.54  23317.61   
2023-02-26 00:00:00+00:00  23561.21  23308.21  23958.02  24033.94  23420.09   
2023-02-27 00:00:00+00:00  23522.87  23321.14  23857.43  23909.67  23530.19   
2023-02-28 00:00:00+00:00  23147.35  23331.54  23647.20  23778.53  23605.28   
2023-03-01 00:00:00+00:00  23701.90  23425.68  23555.40  23653.28  23717.85   

                                 21        50       100       200      EMA9  \
Date                                                                          
2023-02-25 00:00:00+00:00  23253.28  22188.45  19496.61  19760.12  23715.97   
2023-02-26 00:00:00+00:00  23282.11  22320.57  19565.24  19758.19  23685.02   
2023-02-27 00:00:00+00:00  23318.44  22449.21  19633.36  19756.01  23652.59   
2023-02-28 00:00:00+00:00  23312.87  22568.22  19701.91  19749.74  23551.54   
2023-03-01 00:00:00+00:00  23349.18  22693.34  19781.06  19746.13  23581.61   

                             RSI  
Date                              
2023-02-25 00:00:00+00:00  51.42  
2023-02-26 00:00:00+00:00  61.54  
2023-02-27 00:00:00+00:00  62.62  
2023-02-28 00:00:00+00:00  58.43  
2023-03-01 00:00:00+00:00  61.89

In [ ]:
# Quando o preço cruzar acima da média, retorna indicador=True

# teste com média móvel simples de 9 periodos
btc["Cross Above EMA9"] = btc.Close.vbt.crossed_above(btc["EMA9"])
btc.tail()

Close       MMA20            8             9  \
Date                                                                         
2023-02-25 00:00:00+00:00  23175.38  23268.1585  24093.03250  24145.540000   
2023-02-26 00:00:00+00:00  23561.21  23308.2135  23958.02375  24033.941111   
2023-02-27 00:00:00+00:00  23522.87  23321.1425  23857.42750  23909.673333   
2023-02-28 00:00:00+00:00  23147.35  23331.5400  23647.20250  23778.530000   
2023-03-01 00:00:00+00:00  23701.90  23425.6830  23555.39625  23653.280000   

                                     17            21          50         100  \
Date                                                                            
2023-02-25 00:00:00+00:00  23317.610000  23253.278095  22188.4506  19496.6076   
2023-02-26 00:00:00+00:00  23420.090588  23282.113333  22320.5732  19565.2419   
2023-02-27 00:00:00+00:00  23530.190000  23318.435238  22449.2078  19633.3551   
2023-02-28 00:00:00+00:00  23605.276471  23312.866667  22568.2238  19701.9103   
2023-03-01 00:00:00+00:00  23717.847059  23349.176190  22693.3360  19781.0565   

                                   200          EMA9        RSI  \
Date                                                              
2023-02-25 00:00:00+00:00  19760.12025  23715.967607  51.424769   
2023-02-26 00:00:00+00:00  19758.18810  23685.016086  61.542427   
2023-02-27 00:00:00+00:00  19756.01480  23652.586869  62.617074   
2023-02-28 00:00:00+00:00  19749.73745  23551.539495  58.427647   
2023-03-01 00:00:00+00:00  19746.12660  23581.611596  61.893752   

                           Cross Above EMA9  
Date                                         
2023-02-25 00:00:00+00:00             False  
2023-02-26 00:00:00+00:00             False  
2023-02-27 00:00:00+00:00             False  
2023-02-28 00:00:00+00:00             False  
2023-03-01 00:00:00+00:00              True

In [ ]:
# Cruzando abaixo
btc["Cross Below EMA9"] = btc.Close.vbt.crossed_below(btc["EMA9"])
btc["Cross Below EMA9"]

Date
2017-01-01 00:00:00+00:00    False
2017-01-02 00:00:00+00:00    False
2017-01-03 00:00:00+00:00    False
2017-01-04 00:00:00+00:00    False
2017-01-05 00:00:00+00:00    False
                             ...  
2023-02-25 00:00:00+00:00    False
2023-02-26 00:00:00+00:00    False
2023-02-27 00:00:00+00:00    False
2023-02-28 00:00:00+00:00    False
2023-03-01 00:00:00+00:00    False
Freq: D, Name: Cross Below EMA9, Length: 2251, dtype: bool

## AND e Or

Essa é uma parte crucial para a realização do backtesting, o método AND(E) OR(OU) é o que vamos utilizar para definir nossa estratégia, novamente, se a condição for verdadeira ou falsa é retornado TRUE or FALSE, valores que serão armazenados ao nosso dataframe.

A parit daqui vamo utilizar o dataframe btc_ohlc criado no inicio do notebook.

In [ ]:
#criando Médias móveis Aritimética para btc
MMA_btc = vbt.MA.run(btc_ohlc.Close,[9,20,200])

# Estrategia quando MM9  estiver acima da MM20 "E" a MM20 acima da MM200
MMA_btc[9].ma_above(MMA_btc[20]).vbt.signals.AND(MMA_btc[20].ma_above(MMA_btc[200]))

Date
2016-06-16 00:00:00+00:00    False
2016-06-17 00:00:00+00:00    False
2016-06-18 00:00:00+00:00    False
2016-06-19 00:00:00+00:00    False
2016-06-20 00:00:00+00:00    False
                             ...  
2023-02-25 00:00:00+00:00     True
2023-02-26 00:00:00+00:00     True
2023-02-27 00:00:00+00:00     True
2023-02-28 00:00:00+00:00     True
2023-03-01 00:00:00+00:00     True
Freq: D, Length: 2450, dtype: bool

In [ ]:
#Quantos sinais ocorreram?
MMA_btc[9].ma_above(MMA_btc[20]).vbt.signals.AND(MMA_btc[20].ma_above(MMA_btc[200])).sum()

779

In [ ]:
# visualizar estrategia
# Criando Figura com os valores 
fig_MA_all = btc_ohlc.vbt.ohlc.plot()
# adicionando médias recém criadas à plotagem
MMA_btc.ma.vbt.plot(fig=fig_MA_all).show()

In [ ]:
# Gerar o sinal quando a MM9 estiver acima da MM20 "OU" MM20 estiver acima da MM200
MMA_btc[9].ma_above(MMA_btc[20]).vbt.signals.OR(MMA_btc[20].ma_above(MMA_btc[200])).sum()

1816

### Quantificar sequencia de sinais
Vamos ver agora atribuir uma condição, quando o preço fechou acima da EMA9 períodos, retorna True e adciona ao dataframe


In [ ]:
# Obtendo dados do mês de março de 2022
btc_mar = vbt.YFData.download("BTC-USD", start="2022-03-01", end="2022-03-31", interval="1d").get(["Open","High","Low","Close"])
btc_mar["ema9"] = vbt.MA.run(btc_ohlc.Close,9, short_name="MME_9P", ewm=True).ma
btc_mar.dropna(inplace=True)

In [ ]:
# Criando coluna do dataframe com a condição --> Fechamento Acima da EMA9 
btc_mar["Close_Above_EMA9"] = btc_mar.Close >= btc_mar.ema9

# o método pos_rank() acumula os valores, dessa forma podemos ver por quanto tempo o preço se manteve acima da EMA9
btc_mar.Close_Above_EMA9.vbt.signals.pos_rank()

Date
2022-03-01 00:00:00+00:00     0
2022-03-02 00:00:00+00:00     1
2022-03-03 00:00:00+00:00     2
2022-03-04 00:00:00+00:00    -1
2022-03-05 00:00:00+00:00    -1
2022-03-06 00:00:00+00:00    -1
2022-03-07 00:00:00+00:00    -1
2022-03-08 00:00:00+00:00    -1
2022-03-09 00:00:00+00:00     0
2022-03-10 00:00:00+00:00    -1
2022-03-11 00:00:00+00:00    -1
2022-03-12 00:00:00+00:00    -1
2022-03-13 00:00:00+00:00    -1
2022-03-14 00:00:00+00:00     0
2022-03-15 00:00:00+00:00     1
2022-03-16 00:00:00+00:00     2
2022-03-17 00:00:00+00:00     3
2022-03-18 00:00:00+00:00     4
2022-03-19 00:00:00+00:00     5
2022-03-20 00:00:00+00:00     6
2022-03-21 00:00:00+00:00     7
2022-03-22 00:00:00+00:00     8
2022-03-23 00:00:00+00:00     9
2022-03-24 00:00:00+00:00    10
2022-03-25 00:00:00+00:00    11
2022-03-26 00:00:00+00:00    12
2022-03-27 00:00:00+00:00    13
2022-03-28 00:00:00+00:00    14
2022-03-29 00:00:00+00:00    15
2022-03-30 00:00:00+00:00    16
Freq: D, Name: Close_Above_EMA9, dt

In [ ]:
# Aqui retorna um ARRAY com os retornos acumulados
# A primeira vez que o preço fechou acima, permaneceu por 3 dias, na segunda vez apenas um dia, na terceira vez por 17 dias
btc_mar.Close_Above_EMA9.vbt.signals.partition_ranges().duration.values

array([ 3,  1, 17])

##VBT Backtesting

Agora vamos dar inicio ao Backtesting, utilizando uma estratégia simples de cruzamento do preço e média movel. Vamos criar uma dataframe chamado btc_close. 

Para calcular a taxa(fee) = 0.01 = 1% portanto 0.1% = 0.001

In [ ]:
# criando dataframe
btc_close = btc_D.get("Close")
btc_close.tail()

Date
2023-02-25 00:00:00+00:00    23175.375000
2023-02-26 00:00:00+00:00    23561.212891
2023-02-27 00:00:00+00:00    23522.871094
2023-02-28 00:00:00+00:00    23147.353516
2023-03-01 00:00:00+00:00    23701.898438
Freq: D, Name: Close, dtype: float64

In [ ]:
# Calulando média móvel exponencial de 144 períodos
EMA144 = vbt.MA.run(btc_close,144, short_name="EMA",ewm=True).ma

In [ ]:
# Definindo quais serão as condições de entrada e saída
entradas = btc_close.vbt.crossed_above(EMA144)
saidas = btc_close.vbt.crossed_below(EMA144)

###Portfolio
É o pacote da vectorbt que contém diversos métodos que realizam todos os calculos referentes à backtesting.



from_signals() ---> É preciso informar o dataframe com o preço, as condições de entrada e saída, qual o valor da taxa cobrada pela corretora, o que é muito importante ser definido pois dependendo da corretora, se houver uma taxa muito alta, o retorno do backtesting será desconexo com a realidade.

Para calcular a taxa(fee) = 0.01 = 1% portanto 0.1% = 0.001

In [ ]:
portfolio_btc = vbt.Portfolio.from_signals(btc_close,
                                          entradas,
                                          saidas,
                                          fees=0.0005,
                                          direction="both",
                                          freq="D")


####Plotando informações

Agora vamos imprimir os resultados, o método `stats()` retorna uma série de informações como Retorno%, Custo de Taxas, Drawdown, diversas métricas. Vamos chamar esse método e já transformá-lo em um Dataframe para facilitar a visualização.

In [ ]:
#Para criar um dataframe completo com todas as informações
metricas = pd.DataFrame(portfolio_btc.stats())

In [ ]:
# criando um dataframe somente com informações de retorno
retornos = metricas.iloc[3:22]
retornos

0
Start Value                                       100.0
End Value                                  16091.281187
Total Return [%]                           15991.281187
Benchmark Return [%]                        2992.999023
Max Gross Exposure [%]                            100.0
Total Fees Paid                              141.739485
Max Drawdown [%]                              65.776656
Max Drawdown Duration                 552 days 00:00:00
Total Trades                                         46
Total Closed Trades                                  45
Total Open Trades                                     1
Open Trade PnL                              2567.860555
Win Rate [%]                                  28.888889
Best Trade [%]                               938.340708
Worst Trade [%]                               -8.878901
Avg Winning Trade [%]                        128.497862
Avg Losing Trade [%]                          -3.525651
Avg Winning Trade Duration  148 days 01:50:46.153846152
Avg Losing Trade Duration               6 days 03:00:00

In [ ]:
# criando dataframe com as razões
ratios = metricas.iloc[22:]
ratios

0
Profit Factor     6.94428
Expectancy     298.298236
Sharpe Ratio      1.51174
Calmar Ratio       1.7206
Omega Ratio      1.301038
Sortino Ratio    2.425826

* PROFIT FACTOR = O Fator de Lucro é a divisão do Lucro Bruto pelo Prejuízo Bruto.

* EXPECTANCY = Taxa de acerto X Média de Ganhos - (1-Taxa de Acerto) X Média de Perda

* SHARPE RATIO = Valor Ajustado ao Risco -> Valor do Retorno do portfolio subtraido pelo RiskFree(Indicada, ex:SELIC) / volatilidade do portfolio 

* CALMAR RATIO = Média Anual de Retorno / Drawdown MAX

* OMEGA RATIO = Somatorio das posições vencedoras subtraido o benchmarck / somatorio do benchmark subtraido das posições perdedoras

* SORTINO RATIO = Mesma métrica do SHARPE RATIO porém não utiliza o risco global da carteira, somente os riscos dos retornos menores que zero, relativos à perda. 


In [ ]:
#
portfolio_btc.plot(width=800, height=700).show()

In [ ]:
# Evolução do portfolio 
portfolio_btc.plot(subplots=["cash","assets","value"],width=800, height=700).show()

In [ ]:
fig = btc_close.vbt.plot(trace_kwargs=dict(name='Close'))
EMA144.vbt.plot(trace_kwargs=dict(name='MMA'), fig=fig)
portfolio_btc.positions.plot(fig=fig).show()

In [ ]:
# Explorando as ordens
portfolio_btc.orders.records_readable.tail()

Order Id  Column                 Timestamp      Size         Price  \
41        41       0 2021-09-30 00:00:00+00:00  0.347688  43790.894531   
42        42       0 2021-12-04 00:00:00+00:00  0.334538  49200.703125   
43        43       0 2022-03-25 00:00:00+00:00  0.370767  44348.730469   
44        44       0 2022-04-06 00:00:00+00:00  0.406960  43206.738281   
45        45       0 2023-01-13 00:00:00+00:00  0.882281  19909.574219   

        Fees  Side  
41  7.612774   Buy  
42  8.229748  Sell  
43  8.221522   Buy  
44  8.791705  Sell  
45  8.782918   Buy

##Construindo um Portfolio

Vamos criar uma lista com todas os ativos que queremos que faça parte da carteira, e então análisar o desempenho da propria carteira dentro da estratégia definida. 

In [ ]:
# Criando lista com as moedas
lista_moedas = ["BTC-USD","ETH-USD"]

# Obtendo valores de fechamento
carteira = vbt.YFData.download(lista_moedas, start="2014", end="now").get("Close")
carteira.tail()

/usr/local/lib/python3.8/dist-packages/vectorbt/data/base.py:527: UserWarning:

Symbols have mismatching index. Setting missing data points to NaN.



symbol                          BTC-USD      ETH-USD
Date                                                
2023-02-25 00:00:00+00:00  23175.375000  1594.914917
2023-02-26 00:00:00+00:00  23561.212891  1640.817139
2023-02-27 00:00:00+00:00  23522.871094  1634.326416
2023-02-28 00:00:00+00:00  23147.353516  1605.895142
2023-03-01 00:00:00+00:00  23546.951172  1655.244629

In [ ]:
# definindo a alocação da carteira
alocacao = pd.DataFrame.vbt.empty_like(carteira, fill_value=np.nan)

# Percentual alocado em cada ativo no primeiro dia do DataFrame
alocacao.iloc[0]=[0.50,0.50]

#Para alterar a aloação ao longo do DataFrame basta trocar o valor do iloc[] 

In [ ]:
#Construindo o Portfolio

portfolio = vbt.Portfolio.from_orders(
    close = carteira,
    #quantidade
    size = alocacao,
    # tipo da alocacao, no caso, a quantidade informada é em % 
    size_type = "targetpercent",
    group_by=True, #Para plotar com todos os ativos juntos
    cash_sharing=True,  #divide o dinheiro disponivel entre os ativos
    init_cash = 1000,
    freq = "d",
    )

### Opçoes do sizetype
#   Amount = quantidade de ações/moedas
#   Value = quantidade monetaria

In [ ]:
# Imprimindo estatísticas básicas
portfolio.stats(settings=dict(risk_free = 0, freq="d"))

Start                         2014-09-17 00:00:00+00:00
End                           2023-03-01 00:00:00+00:00
Period                               3088 days 00:00:00
Start Value                                      1000.0
End Value                                  26243.712916
Total Return [%]                            2524.371292
Benchmark Return [%]                         2732.29076
Max Gross Exposure [%]                        99.327689
Total Fees Paid                                     0.0
Max Drawdown [%]                              81.487623
Max Drawdown Duration                1079 days 00:00:00
Total Trades                                          1
Total Closed Trades                                   0
Total Open Trades                                     1
Open Trade PnL                             25243.712916
Win Rate [%]                                        NaN
Best Trade [%]                                      NaN
Worst Trade [%]                                 

SHARPE RATIO = Valor Ajustado ao Risco -> Valor do Retorno do portfolio subtraido pelo RiskFree(Indicada, ex:SELIC) / volatilidade do portfolio 

CALMAR RATIO = Média Anual de Retorno / Drawdown MAX

SORTINO RATIO = Mesma métrica do SHARPE RATIO porém não utiliza o risco global da carteira, somente os riscos dos retornos menores que zero, relativos à perda. 

OMEGA RATIO = Somatorio das posições vencedoras subtraido o benchmarck / somatorio do benchmark subtraido das posições perdedoras

In [ ]:
# imprimindo razões
portfolio.returns_stats(settings=dict(risk_free = 0, freq="d"))

Start                        2014-09-17 00:00:00+00:00
End                          2023-03-01 00:00:00+00:00
Period                              3088 days 00:00:00
Total Return [%]                           2524.371292
Benchmark Return [%]                        2732.29076
Annualized Return [%]                        47.139086
Annualized Volatility [%]                    63.300998
Max Drawdown [%]                             81.487623
Max Drawdown Duration               1079 days 00:00:00
Sharpe Ratio                                  0.929225
Calmar Ratio                                  0.578482
Omega Ratio                                   1.166549
Sortino Ratio                                 1.362943
Skew                                         -0.092131
Kurtosis                                      9.106683
Tail Ratio                                     1.01818
Common Sense Ratio                            1.498141
Value at Risk                                -0.051762
Alpha     

BETA = Avalia a sensibilidade do ativo em relação ao Benchmark, se for acima de 1 signifca que o ativo é mais volátil, e abaixo de 1 menos volátil.

ALPHA = O retorno em relação ao benchmark 

VALUE AT RISK = Considera o TAIL RATIO como quantos % de chance de ter uma perda de x% ******* A confirmar



In [ ]:
portfolio.plot().show()

/usr/local/lib/python3.8/dist-packages/vectorbt/generic/plots_builder.py:339: UserWarning:

Subplot 'orders' does not support grouped data

/usr/local/lib/python3.8/dist-packages/vectorbt/generic/plots_builder.py:339: UserWarning:

Subplot 'trade_pnl' does not support grouped data



In [ ]:
portfolio.plot_underwater().show()

In [ ]:
portfolio.drawdowns.plot(top_n=100).show()

##Otimização de Parâmetro

A parte principal do backtesting é a métrica à ser utilizada, e cada ativo vai responder diferente para cada indicador que for analisado, da mesma forma que o mesmo ativo pode responder diferente para o mesmo indicador, dependendo do momento em que se encontra no seu ciclo próprio. 

Determinadas estratégias podem funcionar perfeitamente em um *Bull Market*, e também pode responder com um drawdown de 80% se for aplicada em um período de lateralização ou *Bear Market*. 

A Otimização de Parâmetros nos permite avaliar o desempenho de um ativo em diversas condições. Através do gráfico que foi plotado logo acima, podemos separar análise por cada período 
e ver qual a melhor métrica. 


Vamos utilizar o dataframe BTC_CLOSE



In [ ]:
btc_close = vbt.YFData.download("BTC-USD", start="8 years", interval="1d").get("Close")

In [ ]:
# criar uma lista de médias móveis que vai de 5 até 200 periodo
EMA_5_200 = list(range(5,201))
str(EMA_5_200)

'[5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200]'

In [ ]:
# Construindo indicador
# atribuindo lista EMA_5_200 recem criada como parâmetro
EMA_5_200_df = vbt.MA.run(btc_close, EMA_5_200, short_name="EMA",ewm=True).ma
EMA_5_200_df.tail(1)

EMA_window                          5             6             7    \
EMA_ewm                            True          True          True   
Date                                                                  
2023-03-01 00:00:00+00:00  23507.584089  23528.616913  23547.818718   

EMA_window                          8             9             10   \
EMA_ewm                            True          True          True   
Date                                                                  
2023-03-01 00:00:00+00:00  23562.486603  23571.929346  23576.371587   

EMA_window                          11            12            13   \
EMA_ewm                            True          True          True   
Date                                                                  
2023-03-01 00:00:00+00:00  23576.350955  23572.434906  23565.112341   

EMA_window                          14   ...           191           192  \
EMA_ewm                            True  ...          True          True   
Date                                     ...                               
2023-03-01 00:00:00+00:00  23554.769595  ...  21604.882238  21621.053656   

EMA_window                         193           194           195  \
EMA_ewm                           True          True          True   
Date                                                                 
2023-03-01 00:00:00+00:00  21637.36818  21653.823127  21670.415838   

EMA_window                          196           197           198  \
EMA_ewm                            True          True          True   
Date                                                                  
2023-03-01 00:00:00+00:00  21687.143676  21704.004028  21720.994303   

EMA_window                          199           200  
EMA_ewm                            True          True  
Date                                                   
2023-03-01 00:00:00+00:00  21738.111934  21755.354376  

[1 rows x 196 columns]

In [ ]:
# definindo critérios de entrada e saída 
entrada = btc_close.vbt.crossed_above(EMA_5_200_df)
saida = btc_close.vbt.crossed_below(EMA_5_200_df)

In [ ]:
cross_ema = vbt.Portfolio.from_signals(btc_close,
                                         entrada,
                                         saida,
                                         fees = 0.0005,
                                         direction="both",
                                         freq="d",)

In [ ]:
# grafico de retornos
cross_ema.total_return().vbt.plot().update_yaxes(title_text='<b> Retorno total').update_xaxes(title_text='<b> EMA do Cruzamento').show()

In [ ]:
cross_ema.drawdowns.max_drawdown().vbt.plot().show()

In [ ]:
cross_ema.orders.records_readable.head()

Order Id     Column                 Timestamp      Size       Price  \
0         0  (5, True) 2015-03-06 00:00:00+00:00  0.366489  272.722992   
1         1  (5, True) 2015-03-07 00:00:00+00:00  0.723230  276.260986   
2         2  (5, True) 2015-03-13 00:00:00+00:00  0.713124  285.337006   
3         3  (5, True) 2015-03-15 00:00:00+00:00  0.709785  286.393005   
4         4  (5, True) 2015-03-17 00:00:00+00:00  0.706449  285.505005   

       Fees  Side  
0  0.049975  Sell  
1  0.099900   Buy  
2  0.101740  Sell  
3  0.101639   Buy  
4  0.100847  Sell

####Otimização de Parâmetros com mais de uma média
Aqui vamos analisar o famoso par, Death Cross, e Golden Cross, quando duas médias importantes se cruzam para baixo ou para cima. 


In [ ]:
btc_mult_ema =  vbt.YFData.download("BTC-USD", period="max", interval="1d").get(["Close"])

In [ ]:
# obtendo possiveis valores para -> EMA
ema = np.arange(2,201)

In [ ]:
#construindo indicadores EMA, fast and slow, utilizando o método run_combs() -> run combinations 
fast_ema, slow_ema = vbt.MA.run_combs(btc_mult_ema, window=ema,r=2, short_names=["fast","slow"],ewm=True)

In [ ]:
# definindo critérios de entrada e saída 
entrada = fast_ema.ma_crossed_above(slow_ema)
saida = fast_ema.ma_crossed_below(slow_ema)

In [ ]:
# definindo argumentos do portfolio previamente
pf_kwargs = dict(size=np.inf, fees=0.005, freq="1wk", init_cash=100)

In [ ]:
# declarando portfolio
pf = vbt.Portfolio.from_signals(btc_mult_ema,
                               entrada,
                               saida,
                               **pf_kwargs)

In [ ]:
pd.DataFrame(pf.total_profit()).tail()

total_profit
fast_window fast_ewm slow_window slow_ewm              
197         True     199         True       6220.601714
                     200         True       6763.704264
198         True     199         True       6763.704264
                     200         True       6861.248147
199         True     200         True       6658.199721

In [ ]:
fig = pf.total_return().vbt.heatmap(
    x_level = "fast_window", y_level="slow_window", symmetric=True)

fig.show()